In [1]:
from codebase.classes import Particles
from codebase.classes_data import Data
import pandas as pd
import numpy as np
from codebase.file_utils import (
    save_obj,
    load_obj,
    make_folder,
    path_backslash
)
from codebase.ibis import essl, exp_and_normalise, model_phonebook, run_mcmc
from codebase.plot import get_post_df, plot_density
from codebase.run_tlk import model_phonebook
from tqdm import tqdm
from scipy.special import logsumexp
import altair as alt
alt.data_transformers.disable_max_rows()


import pystan

In [2]:
log_dir = 'log/20210906_172020_test_prior_m14//'
data = load_obj('data', log_dir)


In [3]:
data.raw_data

{'random_seed': 0,
 'N': 200,
 'K': 2,
 'J': 6,
 'alpha': array([0., 0., 0., 0., 0., 0.]),
 'beta': array([[1. , 0. ],
        [0.8, 0. ],
        [0.8, 0. ],
        [0. , 1. ],
        [0. , 0.8],
        [0. , 0.8]]),
 'sigma_z': array([0.80622577, 0.80622577]),
 'Phi_corr': array([[1. , 0.2],
        [0.2, 1. ]]),
 'Phi_cov': array([[0.65, 0.13],
        [0.13, 0.65]]),
 'Marg_cov': array([[1.    , 0.52  , 0.52  , 0.13  , 0.104 , 0.104 ],
        [0.52  , 1.    , 0.416 , 0.104 , 0.0832, 0.0832],
        [0.52  , 0.416 , 1.    , 0.104 , 0.0832, 0.0832],
        [0.13  , 0.104 , 0.104 , 1.    , 0.52  , 0.52  ],
        [0.104 , 0.0832, 0.0832, 0.52  , 1.    , 0.416 ],
        [0.104 , 0.0832, 0.0832, 0.52  , 0.416 , 1.    ]]),
 'Theta': array([[0.35 , 0.   , 0.   , 0.   , 0.   , 0.   ],
        [0.   , 0.584, 0.   , 0.   , 0.   , 0.   ],
        [0.   , 0.   , 0.584, 0.   , 0.   , 0.   ],
        [0.   , 0.   , 0.   , 0.35 , 0.   , 0.   ],
        [0.   , 0.   , 0.   , 0.   , 0.584, 

## Run MCMC

In [4]:
posterior_samples = dict()


In [5]:
## model 1 
model_num = 7

sm = load_obj('sm', 'log/compiled_models/model'+str(model_num)+'/')

param_names = model_phonebook(model_num)['param_names']
latent_names = model_phonebook(model_num)['latent_names']
stan_names = model_phonebook(model_num)['stan_names']

fit_run = run_mcmc(
    data.get_stan_data(),
    sm,
    num_samples = 1000,
    num_warmup = 1000,
    adapt_engaged=True,
    num_chains = 1,
    log_dir = './log/20210906_172026_test_prior_m7/'
)
ps = fit_run.extract(permuted=False, pars=param_names)
posterior_samples['batch1'] = ps

In [6]:
## model 2 
model_num = 14

sm = load_obj('sm', 'log/compiled_models/model'+str(model_num)+'/')

param_names = model_phonebook(model_num)['param_names']
latent_names = model_phonebook(model_num)['latent_names']
stan_names = model_phonebook(model_num)['stan_names']

fit_run = run_mcmc(
    data.get_stan_data(),
    sm,
    num_samples = 1000,
    num_warmup = 1000,
    adapt_engaged=True,
    num_chains = 1,
    log_dir = './log/20210906_172020_test_prior_m14//'
)
ps = fit_run.extract(permuted=False, pars=param_names)
posterior_samples['batch2'] = ps

## Run IBIS

In [7]:
# load existing results
ibis=dict()
ibis['seq1'] = load_obj('particles', './log/20210906_172026_test_prior_m7//')
ibis['seq2'] = load_obj('particles', './log/20210906_172020_test_prior_m14//')


In [8]:
gen_model = 0
model_num = 1

for i in ['seq1', 'seq2']:
    print('\n\n %s'%i)
    for name in ['alpha', 'Marg_cov']:
        samples = np.squeeze(ibis[i].particles[name])
        w = exp_and_normalise(ibis[i].weights)
        print('\n\nEstimate')
        print(np.round(np.average(samples,axis=0, weights=w),2))
        # print('\nRead Data')
        # print(np.round(exp_data.raw_data[name],2))



 seq1


Estimate
[-0.03  0.02 -0.06  0.05  0.02 -0.03]


Estimate
[[0.98 0.53 0.46 0.04 0.03 0.03]
 [0.53 1.01 0.4  0.03 0.03 0.03]
 [0.46 0.4  0.87 0.03 0.02 0.03]
 [0.04 0.03 0.03 0.9  0.48 0.52]
 [0.03 0.03 0.02 0.48 0.99 0.43]
 [0.03 0.03 0.03 0.52 0.43 1.  ]]


 seq2


Estimate
[-0.03  0.01 -0.06  0.05  0.02 -0.02]


Estimate
[[0.99 0.53 0.46 0.03 0.03 0.03]
 [0.53 1.01 0.4  0.03 0.02 0.02]
 [0.46 0.4  0.86 0.02 0.02 0.02]
 [0.03 0.03 0.02 0.91 0.49 0.52]
 [0.03 0.02 0.02 0.49 1.   0.43]
 [0.03 0.02 0.02 0.52 0.43 1.  ]]


## Plot Both results

In [9]:
particles=dict()
# have to resample particles to get rid of weights
for i in ['seq1', 'seq2']:
    ibis[i].resample_particles()
    particles[i] = ibis[i].particles


In [10]:
param = 'beta'
df = get_post_df(np.squeeze(posterior_samples['batch1'][param]))
df['source'] = 'mcmc-1'

df2 = get_post_df(np.squeeze(posterior_samples['batch2'][param]))
df2['source'] = 'mcmc-2'

df3 = get_post_df(particles['seq1'][param])
df3['source'] = 'ibis-1'

df4 = get_post_df(particles['seq2'][param])
df4['source'] = 'ibis-2'

plot_density(pd.concat([df, df2, df3, df4]))

INFO:numexpr.utils:Note: NumExpr detected 24 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


alt.Chart(...)

In [11]:
param = 'alpha'
df = get_post_df(np.squeeze(posterior_samples['batch1'][param]))
df['source'] = 'mcmc-1'

df2 = get_post_df(np.squeeze(posterior_samples['batch2'][param]))
df2['source'] = 'mcmc-2'

df3 = get_post_df(particles['seq1'][param])
df3['source'] = 'ibis-1'

df4 = get_post_df(particles['seq2'][param])
df4['source'] = 'ibis-2'

plot_density(pd.concat([df, df2, df3, df4]))

alt.Chart(...)